### Load libraries and external data

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from data import dataloader
import json
from neuralnet import nn
import numpy as np
import pandas as pd
import pixiedust_node

Pixiedust database opened successfully


#### Load data from Firebase.
Requires [Firebase service account credentials](https://console.firebase.google.com/project/tingle-pilot-collected-data/settings/serviceaccounts/adminsdk) in JSON format saved in `./firebase-credentials`.

In [3]:
pilot_data = dataloader.break_out_blocks(
    dataloader.load_from_firebase()
)

pixiedust_node 0.2.5 started. Cells starting '%%node' may contain Node.js code.
Data loaded from Firebase!


#### Load [Synaptic](http://caza.la/synaptic/)
If you don't have Synaptic installed globally, create and run this cell:

```sh
!npm install -g synaptic
```

If you don't wand Synaptic installed globally, create and run these two cells:

1. ```
cd neuralnet
```

2. ```sh
!npm init -y
!npm install -s synaptic
```

In [4]:
%%node
var lstm = require('../../tingle-pilot-study/neuralnet/lstm.js');

---
### See all targets, number of available samples and iteration blocks

In [5]:
for target in list(pilot_data.target.unique()):
    ib =max(
        pilot_data.loc[
            pilot_data.target==target
        ].iteration_block.dropna()
    )
    print(": ".join([
        target,
        "{0} on-target samples in {1} iteration block{2}".format(
            str(len(pilot_data.loc[
                (pilot_data.target == target) &
                (pilot_data.ontarget)
            ])),
            "%.0f" % ib,
            "s" if ib != 1 else ""
        )
    ]))

none: 19 on-target samples in 2 iteration blocks
environment: 106 on-target samples in 4 iteration blocks
body: 101 on-target samples in 2 iteration blocks
cup: 33 on-target samples in 3 iteration blocks
food: 35 on-target samples in 4 iteration blocks
nails: 69 on-target samples in 3 iteration blocks
smoke: 92 on-target samples in 3 iteration blocks
eyebrow: 235 on-target samples in 5 iteration blocks
nose: 249 on-target samples in 4 iteration blocks
above-ear: 403 on-target samples in 5 iteration blocks
behind-ear: 220 on-target samples in 4 iteration blocks
opposite-cheek: 74 on-target samples in 6 iteration blocks
chin: 166 on-target samples in 1 iteration block
cheek: 686 on-target samples in 6 iteration blocks
forehead: 176 on-target samples in 1 iteration block
top-head: 160 on-target samples in 1 iteration block
back-head: 170 on-target samples in 1 iteration block
opposite-face: 381 on-target samples in 2 iteration blocks
paint-mouth: 81 on-target samples in 3 iteration blocks

---
### Extract training and testing data
Define targets of interest and corresponding offtargets

In [6]:
with open(
    'data/targets.json',
    'r'
) as fp:
    targets = json.load(
        fp
    )[0]

Get training inputs and outputs, inputs that should evaluate ~true and inputs that should evaluate ~false

In [7]:
data = {}
for target in targets:
    data[target] = {
        "train": nn.define_trainer_data(
            pilot_data,
            {
                "target": [target],
                "offtarget": targets[target]
            },
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            100
        ),
        "test_true": nn.define_activation(
            pilot_data,
            [target],
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100
        ),
        "test_false": nn.define_activation(
            pilot_data,
            targets[target],
            [
                "distance",
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100
        )
    }

Preview all inputs and training outputs

In [8]:
data

{'above-ear': {'test_false': [[0.0,
    0.8183760683760684,
    0.8719646799116998,
    0.8660812294182219,
    0.8551042810098793],
   [0.0,
    0.8162393162393163,
    0.8719646799116998,
    0.8507135016465424,
    0.8375411635565313],
   [0.0,
    0.811965811965812,
    0.870860927152318,
    0.8342480790340286,
    0.8342480790340286],
   [0.0,
    0.811965811965812,
    0.858719646799117,
    0.8441273326015369,
    0.8441273326015369],
   [0.0,
    0.8205128205128205,
    0.8664459161147904,
    0.8562019758507136,
    0.8616904500548848],
   [0.0,
    0.8322649572649574,
    0.8730684326710817,
    0.8496158068057081,
    0.8616904500548848],
   [0.6095617529880478,
    0.8376068376068377,
    0.9061810154525386,
    0.8957189901207464,
    0.8902305159165752],
   [0.0,
    0.8429487179487181,
    0.9061810154525386,
    0.9088913282107575,
    0.8792535675082327],
   [0.09163346613545817,
    0.8429487179487181,
    0.9094922737306844,
    0.9055982436882547,
    0.87925356750

**Note**: These data take some time to copy across environments. Give the notebook some time between running cells across Python and JavaScript.

---
### Train and test

In [9]:
target = "above-ear"
training_data = data[target]["train"]

In [13]:
%%node
for(var i=0; i < training_data.length; i++){
    training_data[i].output = [Math.round(training_data[i].output)]
}

... ...


In [14]:
%%node
aboveEar = lstm.train_lstm([5,5,2,1], training_data, 0.06, 0.06, 3000);

TRAINING 🏋 interations:3000 🏋 minimum error:0.06 🏋 rate:0.06
iterations 5 error 0.1280686352789778 rate 0.06
iterations 10 error 0.12246275324156933 rate 0.06
iterations 15 error 0.12284769499381835 rate 0.06
iterations 20 error 0.12097159051375374 rate 0.06
iterations 25 error 0.12125802350640145 rate 0.06
iterations 30 error 0.12014601659736086 rate 0.06
iterations 35 error 0.11963540489897935 rate 0.06
iterations 40 error 0.11851854812898503 rate 0.06
iterations 45 error 0.11916343044875671 rate 0.06
iterations 50 error 0.11916976789794163 rate 0.06
iterations 55 error 0.11817725960485471 rate 0.06
iterations 60 error 0.11805468644743146 rate 0.06
iterations 65 error 0.11595129147332589 rate 0.06
iterations 70 error 0.1169137049101284 rate 0.06
iterations 75 error 0.11681479253679053 rate 0.06
iterations 80 error 0.11644999288042869 rate 0.06
iterations 85 error 0.11571315870777882 rate 0.06
iterations 90 error 0.11518420203992304 rate 0.06
iterations 95 error 0.11566146442140014 ra

iterations 810 error 0.0913037813983756 rate 0.06
iterations 815 error 0.08991302050531566 rate 0.06
iterations 820 error 0.0901494887543506 rate 0.06
iterations 825 error 0.08768496071042757 rate 0.06
iterations 830 error 0.08953220521336748 rate 0.06
iterations 835 error 0.088102933402281 rate 0.06
iterations 840 error 0.089103454177262 rate 0.06
iterations 845 error 0.0894656342113128 rate 0.06
iterations 850 error 0.09008527789747174 rate 0.06
iterations 855 error 0.08779036648471253 rate 0.06
iterations 860 error 0.0880466435195841 rate 0.06
iterations 865 error 0.08939435344611123 rate 0.06
iterations 870 error 0.08926479502951583 rate 0.06
iterations 875 error 0.0888905915028824 rate 0.06
iterations 880 error 0.0864586204370835 rate 0.06
iterations 885 error 0.08926433251742477 rate 0.06
iterations 890 error 0.08825144498375624 rate 0.06
iterations 895 error 0.08807816398713184 rate 0.06
iterations 900 error 0.08868232737046061 rate 0.06
iterations 905 error 0.08797874532339221 

iterations 1605 error 0.0816018033479066 rate 0.06
iterations 1610 error 0.08374932331414152 rate 0.06
iterations 1615 error 0.08340832125215121 rate 0.06
iterations 1620 error 0.08283425045024378 rate 0.06
iterations 1625 error 0.08178600961939411 rate 0.06
iterations 1630 error 0.08205547538230255 rate 0.06
iterations 1635 error 0.08169575496094367 rate 0.06
iterations 1640 error 0.08202406660298342 rate 0.06
iterations 1645 error 0.08198868844999153 rate 0.06
iterations 1650 error 0.08140281264816668 rate 0.06
iterations 1655 error 0.0813038363863444 rate 0.06
iterations 1660 error 0.08212386147568748 rate 0.06
iterations 1665 error 0.08237782259617485 rate 0.06
iterations 1670 error 0.08281497849364053 rate 0.06
iterations 1675 error 0.0822470402118729 rate 0.06
iterations 1680 error 0.08166106660448699 rate 0.06
iterations 1685 error 0.08299864272894214 rate 0.06
iterations 1690 error 0.08056463296847799 rate 0.06
iterations 1695 error 0.08190074773760392 rate 0.06
iterations 1700

iterations 2400 error 0.07860310649838116 rate 0.06
iterations 2405 error 0.07735483371334963 rate 0.06
iterations 2410 error 0.07693591439981197 rate 0.06
iterations 2415 error 0.07868002864228418 rate 0.06
iterations 2420 error 0.07789386234671423 rate 0.06
iterations 2425 error 0.07819148708169812 rate 0.06
iterations 2430 error 0.07797577020033856 rate 0.06
iterations 2435 error 0.07870412433070012 rate 0.06
iterations 2440 error 0.07566782821836986 rate 0.06
iterations 2445 error 0.07512881914778878 rate 0.06
iterations 2450 error 0.07772024316756004 rate 0.06
iterations 2455 error 0.07951575150423693 rate 0.06
iterations 2460 error 0.07782503156919529 rate 0.06
iterations 2465 error 0.075910436398053 rate 0.06
iterations 2470 error 0.07773049607907394 rate 0.06
iterations 2475 error 0.07656282950405167 rate 0.06
iterations 2480 error 0.07778088252262913 rate 0.06
iterations 2485 error 0.07812025947251104 rate 0.06
iterations 2490 error 0.07769959436814919 rate 0.06
iterations 249

In [16]:
%%node
var test_outputs = {"true":[],"false":[]};
for(var iteration=0; iteration < data["above-ear"]["test_true"].length; iteration++){
  test_outputs["true"].push(aboveEar.activate(data["above-ear"]["test_true"][iteration]));
  }
for(var iteration=0; iteration < data["above-ear"]["test_false"].length; iteration++){
  test_outputs["false"].push(aboveEar.activate(data["above-ear"]["test_false"][iteration]));
}

... ...
... ...


In [17]:
test_outputs

{'false': [[0.0005528216981357794],
  [0.00013623311297543305],
  [2.110332408078167e-05],
  [9.792854289477434e-05],
  [0.0002956954778503984],
  [0.000298726173267885],
  [6.038358016796562e-07],
  [0.044443987376660735],
  [0.006071311452866783],
  [0.08360669343859548],
  [0.033166517664011144],
  [0.030951252958382178],
  [0.0019523785886970716],
  [0.12489901118358009],
  [0.06414969373885415],
  [0.04376541128693362],
  [0.015127818594827534],
  [0.07114266316476214],
  [0.07629663700003556],
  [0.022145747815507013],
  [0.00888009897768011],
  [0.09164833063881898],
  [0.031123193569717125],
  [0.03888110872307439],
  [0.01329882912134735],
  [0.01697982953253921],
  [0.01809248313703144],
  [0.040833957592739833],
  [0.02821101391553266],
  [0.023797510670099976],
  [0.031431383846911784],
  [0.0030499660604483103],
  [0.09590910329945526],
  [0.029750123141448544],
  [0.02215755302366743],
  [0.013807561209211535],
  [0.03537136003060602],
  [0.055600689284478616],
  [0.01802

---
### See outputs

If the training is adequate x ≈ 0 ∀ x in the following:

In [22]:
f = [
        outputs for outputs in test_outputs['false']
    ]
f

[0.0005528216981357794,
 0.00013623311297543305,
 2.110332408078167e-05,
 9.792854289477434e-05,
 0.0002956954778503984,
 0.000298726173267885,
 6.038358016796562e-07,
 0.044443987376660735,
 0.006071311452866783,
 0.08360669343859548,
 0.033166517664011144,
 0.030951252958382178,
 0.0019523785886970716,
 0.12489901118358009,
 0.06414969373885415,
 0.04376541128693362,
 0.015127818594827534,
 0.07114266316476214,
 0.07629663700003556,
 0.022145747815507013,
 0.00888009897768011,
 0.09164833063881898,
 0.031123193569717125,
 0.03888110872307439,
 0.01329882912134735,
 0.01697982953253921,
 0.01809248313703144,
 0.040833957592739833,
 0.02821101391553266,
 0.023797510670099976,
 0.031431383846911784,
 0.0030499660604483103,
 0.09590910329945526,
 0.029750123141448544,
 0.02215755302366743,
 0.013807561209211535,
 0.03537136003060602,
 0.055600689284478616,
 0.018025978406512065,
 0.02658676076255791,
 0.04613091816689675,
 0.013100784509241915,
 0.01635285815064306,
 0.05574539503508443,

If the training is adequate x ≈ 1 ∀ x in the following:

In [23]:
t = [
        outputs for outputs in test_outputs['true']
    ]
t

[[0.07811730464727255],
 [0.018173372512054576],
 [0.019913276020988153],
 [0.07139543319384876],
 [0.038032247962844906],
 [0.012821546165690588],
 [0.010893494548067269],
 [0.03106330597446699],
 [0.04295851931860811],
 [0.0393408244361766],
 [0.20069778509245675],
 [0.12667922023133596],
 [0.05577380329146384],
 [0.015523703844033286],
 [0.040885344065422005],
 [0.0846809809854574],
 [0.11966254368001994],
 [0.09226535650199486],
 [0.038283268825302794],
 [0.12288773838747999],
 [0.09519349395997369],
 [0.05675587937477335],
 [0.009911297785203716],
 [0.12463967689918004],
 [0.09882001478362816],
 [0.11471401683744034],
 [0.025677577563253274],
 [0.11420321887832309],
 [0.09090894643892976],
 [0.05209785030931109],
 [0.014035932884827285],
 [0.0005377521791540936],
 [0.001785597016372941],
 [0.006931189310604142],
 [0.02409613566942677],
 [0.04263983097909658],
 [0.010104676025482696],
 [0.07482127935405619],
 [0.03986524438060128],
 [0.05557106002826281],
 [0.04911544812051851],
 [

Finally, if training is adequate, f ≪ t:

In [24]:
f_mean = np.mean(f)
t_mean = np.mean(t)
print(
    "f = {0}\nt = {1}\n{0} ≪ {1} ?".format(
        str(f_mean),
        str(t_mean)
    ) if f_mean < t_mean else "Nope. f > t"
)

f = 0.008127217616084611
t = 0.06624343787793106
0.008127217616084611 ≪ 0.06624343787793106 ?


---
### Try with demo data

In [25]:
with open(
    'data/demo_data.json',
    'r'
) as fp:
    demo_data = json.load(
        fp
    )[0]

In [26]:
scale = list(
    pd.DataFrame(
        [
            a[0:5] for a in [
                *demo_data["true"],
                *demo_data["false"]
            ]
        ]
    ).astype('float').max(axis=0)
)
demo_test = {
    "train":[
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [1]
        } for datum in demo_data["true"][0:40]],
        *[{
            "input": [
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ],
            "output": [0]
        } for datum in demo_data["false"][0:40]]
    ],
    "test_true": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["true"][41:]],
    "test_false": [[
                float(d)/scale[datum_i] for datum_i, d in enumerate(datum[0:5])
            ] for datum in demo_data["false"][41:]]
}

In [27]:
%%node
var LSTM5 = lstm.train_lstm([5,5,2,1], demo_test["train"], 0.06, 0.06, 3000);

TRAINING 🏋 interations:3000 🏋 minimum error:0.06 🏋 rate:0.06
iterations 5 error 0.721277572706658 rate 0.06
iterations 10 error 0.7073211957927998 rate 0.06
iterations 15 error 0.7047239570458155 rate 0.06
iterations 20 error 0.6917489179286229 rate 0.06
iterations 25 error 0.6781289995433194 rate 0.06
iterations 30 error 0.7000719227551062 rate 0.06
iterations 35 error 0.6796970088768075 rate 0.06
iterations 40 error 0.6832108553440933 rate 0.06
iterations 45 error 0.6719418029226507 rate 0.06
iterations 50 error 0.6754528095510779 rate 0.06
iterations 55 error 0.6623696904849903 rate 0.06
iterations 60 error 0.6732814659701603 rate 0.06
iterations 65 error 0.6543464759307855 rate 0.06
iterations 70 error 0.6700387239927236 rate 0.06
iterations 75 error 0.6485038773491218 rate 0.06
iterations 80 error 0.6527691450682407 rate 0.06
iterations 85 error 0.6467867623029596 rate 0.06
iterations 90 error 0.652144284837267 rate 0.06
iterations 95 error 0.6419273967066228 rate 0.06
iterations 

iterations 815 error 0.19069342471727024 rate 0.06
iterations 820 error 0.1613585717181028 rate 0.06
iterations 825 error 0.20463071920682183 rate 0.06
iterations 830 error 0.21729773194778068 rate 0.06
iterations 835 error 0.1944270568474439 rate 0.06
iterations 840 error 0.1833162800547548 rate 0.06
iterations 845 error 0.1860349054113916 rate 0.06
iterations 850 error 0.1877600925100225 rate 0.06
iterations 855 error 0.18622020023307823 rate 0.06
iterations 860 error 0.21798650576364675 rate 0.06
iterations 865 error 0.21546189725686699 rate 0.06
iterations 870 error 0.17470725134334755 rate 0.06
iterations 875 error 0.24038184730693102 rate 0.06
iterations 880 error 0.21985098662880515 rate 0.06
iterations 885 error 0.20584181097166815 rate 0.06
iterations 890 error 0.20784574062970562 rate 0.06
iterations 895 error 0.13561170476123818 rate 0.06
iterations 900 error 0.19609547393481477 rate 0.06
iterations 905 error 0.20843984502014218 rate 0.06
iterations 910 error 0.2217943101171

iterations 1620 error 0.12705295976914047 rate 0.06
iterations 1625 error 0.09899491183673921 rate 0.06
iterations 1630 error 0.14198699553424807 rate 0.06
iterations 1635 error 0.12500206491950078 rate 0.06
iterations 1640 error 0.14739888528552114 rate 0.06
iterations 1645 error 0.10086929851806048 rate 0.06
iterations 1650 error 0.13109774730775756 rate 0.06
iterations 1655 error 0.1163086554848101 rate 0.06
iterations 1660 error 0.12083301612255115 rate 0.06
iterations 1665 error 0.13404495509158904 rate 0.06
iterations 1670 error 0.07971602794261501 rate 0.06
iterations 1675 error 0.13124481951391834 rate 0.06
iterations 1680 error 0.12959934489782202 rate 0.06
iterations 1685 error 0.1073365451681488 rate 0.06
iterations 1690 error 0.13012916641957548 rate 0.06
iterations 1695 error 0.11576498735583889 rate 0.06
iterations 1700 error 0.0998015236247856 rate 0.06
iterations 1705 error 0.13721233995934531 rate 0.06
iterations 1710 error 0.08972939929186954 rate 0.06
iterations 1715

In [29]:
%%node
var demo_test_outputs = {"true":[],"false":[]}
for(var iteration=0; iteration < demo_test["test_true"].length; iteration++){
    var op = LSTM5.activate(demo_test["test_true"][iteration]);
    demo_test_outputs["true"].push(op);
}
for(var iteration=0; iteration < demo_test["test_false"].length; iteration++){
    demo_test_outputs["false"].push(LSTM5.activate(demo_test["test_false"][iteration]));
}

... ... ...
... ...


In [30]:
demo_test_outputs

{'false': [[0.8329438386061621],
  [0.9226415878744636],
  [0.715019380608519],
  [0.3214371324651962],
  [0.00601816653126712],
  [0.0001480250310523145],
  [8.31692760524024e-06],
  [4.0776021473899934e-06],
  [1.4395202162028856e-06]],
 'true': [[0.8379628592243241],
  [0.8141540075364172],
  [0.9915725575559937],
  [0.9941967325856215],
  [0.994437263354661],
  [0.9623216289995543],
  [0.9666514599447125],
  [0.9326328434075669],
  [0.9908564476483857]]}

In [31]:
np.mean(demo_test_outputs['false'])

0.31091355168518103

In [32]:
np.mean(demo_test_outputs['true'])

0.9427539778063596